This notebook will grab the data at a specific time range and plot on a map

In [1]:
# imports

import numpy as np
import pandas as pd
import geopandas
# from geopandas import GeoDataFrame

import sys
sys.path.append("C:\\Users\\beezy\\git\\bluebikes_system_analysis\\code")
sys.path.append("C:\\Users\\beezy\\git\\bluebikes_system_analysis\\code\\data_handling")

# for loading station information
from data_handling.data_loading_methods import load_station_info

# for loading a json and saving to a csv
from data_handling.loadjson_savetocsv import load_jsons_savetocsv

In [2]:
# load data, perform housekeeping, calculate capacity

# read from csv
filetoload = 'C:\\Users\\beezy\\git\\bluebikes_system_analysis\\data\\station data 220715 jsons\\log_220715.csv' 
station_df = pd.read_csv(filetoload, index_col=0) # read csv into df

# drop any duplicates
station_df = station_df.drop_duplicates()

# delete rows with unreal values
station_df = station_df.replace('', np.nan) # this replaces empty strings with NaN quickly
[rows2drop, cols2drop] = np.where(pd.isnull(station_df)) # this uses numpy to find NaN values
station_df = station_df.drop(labels=station_df.index[rows2drop], axis=0)

# extract hour and minute from timestamps
# convert time to datetime
station_df['last_reported'] = pd.to_datetime( station_df['last_reported'], unit='s' )

# add hour, minute column
station_df['hour'] = station_df['last_reported'].dt.hour
station_df['minute'] = station_df['last_reported'].dt.minute

# remove timestamp column, since explore() doesn't like it
station_df = station_df.drop('last_reported', axis=1)

# rename capacity to total_capacity
station_df = station_df.rename(columns={'capacity': 'total_capacity'})

# calculate true capacity
station_df['true_capacity'] = station_df['num_bikes_available']/station_df['total_capacity']

station_df

station_status  num_bikes_available  is_renting  num_docks_disabled  \
0              active                    2           1                   0   
1              active                    6           1                   0   
2              active                   12           1                   0   
3              active                    6           1                   0   
4              active                    0           1                   0   
...               ...                  ...         ...                 ...   
124653         active                    2           1                   1   
124654         active                   10           1                   1   
124690         active                   21           1                   0   
124695         active                    2           1                   0   
124700         active                    1           1                   2   

        is_installed  is_returning  num_docks_available  num_bikes_disabled  \
0                  1             1                   13                   0   
1                  1             1                   12                   1   
2                  1             1                    3                   0   
3                  1             1                    8                   1   
4                  1             1                   15                   0   
...              ...           ...                  ...                 ...   
124653             1             1                   15                   1   
124654             1             1                    8                   0   
124690             1             1                    1                   1   
124695             1             1                   16                   0   
124700             1             1                   16                   0   

        station_id        lon  region_id        lat  \
0                3 -71.100619       10.0  42.340115   
1                4 -71.069616       10.0  42.345392   
2                5 -71.090179       10.0  42.341814   
3                6 -71.065287       10.0  42.361257   
4                7 -71.044571       10.0  42.353391   
...            ...        ...        ...        ...   
124653         514 -71.094644        9.0  42.386736   
124654         515 -71.109988        8.0  42.368952   
124690         553 -71.076198        8.0  42.371141   
124695         558 -71.101246       10.0  42.333293   
124700         563 -71.015137       10.0  42.385181   

                                                     name  total_capacity  \
0       Colleges of the Fenway - Fenway at Avenue Loui...              15   
1                             Tremont St at E Berkeley St              19   
2             Northeastern University - North Parking Lot              15   
3                                  Cambridge St at Joy St              15   
4                                                Fan Pier              15   
...                                                   ...             ...   
124653                      Gilman Square T at Medford St              19   
124654                                       955 Mass Ave              19   
124690           Cambridge Crossing at North First Street              23   
124695                     St. Alphonsus St at Tremont St              18   
124700                          Addison St at Saratoga St              19   

        hour  minute  true_capacity  
0          3      58       0.133333  
1          3      42       0.315789  
2          3      58       0.800000  
3          3      50       0.400000  
4          1      40       0.000000  
...      ...     ...            ...  
124653     3      56       0.105263  
124654     3      53       0.526316  
124690     3      54       0.913043  
124695     3      55       0.111111  
124700     3      57       0.052632  

[22996 rows x 17 columns]

In [3]:
# keep entries in desired timeframe
selected_hour     = 23
selected_min_low  = 0
selected_min_high = 59
station_df_crop = station_df.loc[ station_df['hour'] == selected_hour ]
station_df_crop = station_df_crop.loc[ ( station_df_crop['minute'] >= selected_min_low ) & 
                             ( station_df_crop['minute'] <= selected_min_high ) ]
# station_df_crop

# convert to a geodataframe
station_gdf = geopandas.GeoDataFrame(
    station_df_crop, geometry=geopandas.points_from_xy(station_df_crop['lon'], station_df_crop['lat']), crs='EPSG:4326')

# station_gdf

In [4]:
# plot on explore map
station_gdf.explore(column='true_capacity', 
                    marker_kwds=dict(radius=10, fill=True),
                    cmap='RdYlGn', 
                    vmin=0, vmax=1,
                   location=[42.351, -71.0898],
                   zoom_start=13)

In [14]:
# can i remove a crs?
station_gdf = station_gdf.to_crs(crs='EPSG:2263')

# make a buncha circles sized by capacity
station_gdf['capacitycircs'] = station_gdf['geometry'].buffer( 20*station_gdf['total_capacity'] )

station_gdf.crs



<Derived Projected CRS: EPSG:2263>
Name: NAD83 / New York Long Island (ftUS)
Axis Info [cartesian]:
- X[east]: Easting (US survey foot)
- Y[north]: Northing (US survey foot)
Area of Use:
- name: United States (USA) - New York - counties of Bronx; Kings; Nassau; New York; Queens; Richmond; Suffolk.
- bounds: (-74.26, 40.47, -71.8, 41.3)
Coordinate Operation:
- name: SPCS83 New York Long Island zone (US Survey feet)
- method: Lambert Conic Conformal (2SP)
Datum: North American Datum 1983
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

In [10]:

station_gdf

station_status  num_bikes_available  is_renting  num_docks_disabled  \
170            active                    8           1                   0   
172            active                    6           1                   0   
245            active                   10           1                   0   
258            active                    3           1                   0   
309            active                    1           1                   0   
...               ...                  ...         ...                 ...   
104217         active                   10           1                   0   
104244         active                    4           1                   0   
104273         active                    0           1                   0   
104275         active                   10           1                   0   
104332         active                    2           1                   0   

        is_installed  is_returning  num_docks_available  num_bikes_disabled  \
170                1             1                    2                   0   
172                1             1                    9                   0   
245                1             1                    6                   1   
258                1             1                   10                   2   
309                1             1                   15                   0   
...              ...           ...                  ...                 ...   
104217             1             1                    6                   3   
104244             1             1                   15                   0   
104273             1             1                   19                   0   
104275             1             1                    9                   0   
104332             1             1                   13                   0   

        station_id        lon  region_id        lat  \
170            196 -71.082431       10.0  42.317873   
172            199 -71.069781       10.0  42.318697   
245            355 -71.010631       10.0  42.385224   
258            368 -71.077986       10.0  42.317860   
309            425 -71.096399       10.0  42.319309   
...            ...        ...        ...        ...   
104217         412 -71.066887       10.0  42.343033   
104244         443 -71.092189       10.0  42.332863   
104273         479 -71.089740        8.0  42.363004   
104275         481 -71.039870       10.0  42.341781   
104332         544 -71.108413        8.0  42.357662   

                                                   name  total_capacity  hour  \
170                Roxbury YMCA - Warren St at MLK Blvd              10    23   
172     Uphams Corner T Stop - Magnolia St at Dudley St              15    23   
245                 Bennington St at Constitution Beach              17    23   
258                       Blue Hill Ave at Southwood St              15    23   
309                                   The Dimock Center              16    23   
...                                                 ...             ...   ...   
104217                     Washington St at Peters Park              19    23   
104244                        Whittier St Health Center              19    23   
104273               Galileo Galilei Way at Main Street              19    23   
104275                                    645 Summer St              19    23   
104332                     Old Morse Park at Putnam Ave              15    23   

        minute  true_capacity                        geometry  \
170         16       0.800000  POINT (1773453.331 797028.688)   
172         31       0.400000  POINT (1776863.640 797443.144)   
245         32       0.588235  POINT (1792029.987 822222.555)   
258         59       0.200000  POINT (1774655.279 797063.994)   
309         32       0.062500  POINT (1769658.904 797426.393)   
...        ...            ...                             ...   
104217      59       0.526316  P

In [7]:
station_gdf = station_gdf.set_geometry('capacitycircs')

In [15]:
station_gdf.explore()